In [ ]:
## Code for lecture 3: Compute higher-order SVD
import numpy as np
import matplotlib.pyplot as plt

# Create a tensor from function on grid [-1,1]^d
def fun(x,y,z):
    # E.g.: Slater-type function exp(-||Ax||)
    return 10*np.exp(-np.sqrt(x**2 + 5*y**2 + 10*z**2))

# meshgrid
n1,n2,n3 = 30,40,50
xax = np.linspace(-1,1,n1)
yax = np.linspace(-1,1,n2)
zax = np.linspace(-1,1,n3)
x,y,z = np.meshgrid(xax,yax,zax,indexing='ij')

# Compute tensor as f(xi,y_j,z_k)
Y = fun(x,y,z)
# Alternative: test random tensor
# Y = np.random.randn(n1,n2,n3)
normY = np.linalg.norm(Y)
print(Y.shape)

# Compute SVDs of matricizations
U1, S1, _ = np.linalg.svd(np.reshape(Y,[n1,n2*n3]))
U2, S2, _ = np.linalg.svd(np.reshape(Y.transpose(1,0,2),[n2,n1*n3]))
U3, S3, _ = np.linalg.svd(np.reshape(Y.transpose(2,0,1),[n3,n1*n2]))

# Investigate singular values of matricizations
fig, (ax1, ax2, ax3) = plt.subplots(1, 3, figsize=(7, 2))
ax1.semilogy(S1/normY)
ax2.semilogy(S2/normY)
ax3.semilogy(S3/normY)
fig.tight_layout()
plt.show()

# Truncated HOSVD to m-rank k1,k2,k3
k1,k2,k3 = 3,4,5

# Computation of core tensor by sequential partial contactions
C = np.tensordot(Y,U1[:,:k1],axes=(0,0))
#print(C.shape)
C = np.tensordot(C,U2[:,:k2],axes=(0,0))
#print(C.shape)
C = np.tensordot(C,U3[:,:k3],axes=(0,0))
print(C.shape)

# The resulting full n1,n2,n3 tensor of m-rank k1,k2,k3 could be constructed as follows
X = np.tensordot(C,U1[:,:k1],axes=(0,1))
X = np.tensordot(X,U2[:,:k2],axes=(0,1))
X = np.tensordot(X,U3[:,:k3],axes=(0,1))

# Relative L2 error computed in two ways
print("Relative Frobenius norm error =",np.linalg.norm(Y-X) / normY)
print("Relative Frobenius norm error =",np.sqrt(normY**2 - np.linalg.norm(C)**2) / normY)


In [ ]:
## Code for lecture 3: Higher-order power method

# We continue with the previous example by computing a rank-one approximation using HOPM and comparing with HOSVD
hopm_it = 5
err = np.zeros(hopm_it)

# random initialization
u1,u2,u3 = np.random.randn(n1),np.random.randn(n2),np.random.randn(n3)

# HOSVD initialization
# u1,u2,u3 = U1[:,0],U2[:,0],U3[:,0]

# HOPM algorithm 
for t in range(hopm_it):
    u1 = np.tensordot(np.tensordot(Y,u2,axes=(1,0)),u3,axes=(1,0)) / np.linalg.norm(u2) / np.linalg.norm(u3)
    u2 = np.tensordot(np.tensordot(Y,u1,axes=(0,0)),u3,axes=(1,0)) / np.linalg.norm(u1) / np.linalg.norm(u3)
    u3 = np.tensordot(np.tensordot(Y,u1,axes=(0,0)),u2,axes=(0,0)) / np.linalg.norm(u1) / np.linalg.norm(u2)
    err[t] = np.sqrt(normY**2 - np.linalg.norm(u3)**2) / normY
    
# plot error history
fig, ax = plt.subplots(1, 1, figsize=(2, 2))
ax.semilogy(err)
print("HOPM error = ", err[-1])

# Compare with HOSVD error
sigma = np.tensordot(Y,np.tensordot(U1[:,0],np.tensordot(U2[:,0],U3[:,0],0),0),axes=([0,1,2],[0,1,2]))
print("HOSVD error =", np.sqrt(normY**2 - sigma**2) / normY)
